# Exercise Sheet 1

### 1 - A Boolean circuit

Consider a Boolean logical gate with three inputs (`a`, `b` and `c`), three outputs (`d`, `e` and `f`), and the following truth table:

| `abc` | `def` |
|---|---|
| `000` | `010` |
| `001` | `110` |
| `010` | `001` |
| `011` | `101` |
| `100` | `011` |
| `101` | `000` |
| `110` | `111` |
| `111` | `100` |

Construct a quantum circuit to  implement this truth table, following the example seen in [these](exercises_2022/Exercise2.ipynb) in-class exercises.

### 2 - Circuits for a Bell test

The final part of [Hello Qiskit](https://learn.qiskit.org/course/ch-demos/hello-qiskit) sets up a test of Bell's inequalities. Construct the circuits required for this following the examples seen in [The Unique Properties of Qubits](extra_resources/unique-properties-qubits.ipynb).


### 3 Some two-qubit gates

The controlled-NOT can be expressed in matrix form as

$$\left( \begin{array}{ccc}
1 & 0 & 0 & 0\\
0 & 1 & 0 & 0\\
0 & 0 & 0 & 1\\
0 & 0 & 1 & 0\\
\end{array} \right)$$

Here the control qubit is that on the right side of the tensor product, and the target qubit is on the left.

* (a) Write down the matrix for the case with the control on the left and target on the right.

* (b) Find the eigenvectors and eigenvalues of these matrices.

* (c) The so-called 'SWAP gate' can be built from controlled-NOTs in the following two ways. Show that they have the same matrix form.

```
           ┌───┐     
      ──■──┤ X ├──■──
      ┌─┴─┐└─┬─┘┌─┴─┐
      ┤ X ├──■──┤ X ├
      └───┘     └───┘

      ┌───┐     ┌───┐
      ┤ X ├──■──┤ X ├
      └─┬─┘┌─┴─┐└─┬─┘
      ──■──┤ X ├──■──
           └───┘ 

```

* (d) Find the eigenvectors and eigenvalues of the SWAP gate.

### 4 - Entangled states

Consider the controlled-$Z$ gate

$$
CZ = |1\rangle \langle 1 | \otimes I + |0\rangle \langle 0 | \otimes Z,
$$

and the following two families of states.

$$
|a\rangle \otimes |b\rangle  = (a_0 |0\rangle + a_1 |1\rangle) \otimes (b_0 |0\rangle + b_1 |1\rangle)\\
|a\rangle \otimes |\Phi^+\rangle  = (a_0 |0\rangle + a_1 |1\rangle) \otimes \frac{1}{\sqrt{2}} ( |00\rangle + |11\rangle).
$$

* (a) Apply the $CZ$ gate to the two-qubit state $|a\rangle \otimes |b\rangle$ and find the reduced density matrix for both qubits. Then find the eigenvectors and eigenvalues for these matrices, and show that the eigenvalues are the same for both qubits.

* (b) Apply the $CZ$ gate to the first two qubits of the three qubit state $|a\rangle \otimes |\Phi^+\rangle$. Again find the reduced density matrices, and their eigenvalues and vectors. Are the eigenvalues of both qubits still the same?

## Hints

### 1

The truth table is reversable, so it would be possible to create a solution using only three qubits. But it would also be hard. In the solution I present the least elegant solution that uses 6 qubits in all. They should know that such non-elegant solutions are an option.

### 2

Looking at Hello Qiskit (or otherwise looking up Bell tests) and using the mentioned example should be enough to set them on the right path.

### 3 and 4

Just some matrix stuff. Maybe doing some partial trace examples with them would be good, though.

## Solutions

### Solution 1

In [31]:
from qiskit import QuantumCircuit
from qiskit_aer import AerSimulator
from qiskit.circuit.library.standard_gates import XGate

# create a controlled-controlled-controlled-X gate
# This performs an X on the target qubit if the three controls are all |1>
cccx = XGate().control(3)

def boolean_gate(abc):

    qc = QuantumCircuit(6,3)

    # encode a, b and c in qubits 0, 1 and 2, respectively
    if abc[0]=='1':
        qc.x(0)
    if abc[1]=='1':
        qc.x(1)
    if abc[2]=='1':
        qc.x(2)

    # we'll encode d, e and f in qubits 3, 4 and 5, respectively
    # for each input we'll do the following process
    #     1 - rotate that input to 111
    #     2 - implement cccxs whose targets are any output bits that should be 1
    #     3 - undo step 1
    # This will then prepare the correct outputs (although in a needlessly long way)

    # 000 -> 010
    if abc == '000':
        qc.x([0,1,2])
        qc.append(cccx, [0,1,2, 4])
        qc.x([0,1,2])

    # 001 -> 110
    if abc == '001':
        qc.x([0,1])
        qc.append(cccx, [0,1,2, 3])
        qc.append(cccx, [0,1,2, 4])
        qc.x([0,1])

    # 010 -> 001
    if abc == '010':
        qc.x([0,2])
        qc.append(cccx, [0,1,2, 5])
        qc.x([0,2])

    # and so on for the other inputs that I can't be bothered to do

    # finally we measure the output bits to get the output
    qc.measure([3,4,5], [2,1,0])

    return AerSimulator().run(qc, shots=1, memory=True).result().get_memory()[0]